In [2]:
from transformers import (
    AutoConfig,
    AutoModelForSequenceClassification,
    AutoTokenizer,
    DataCollatorWithPadding,
    EvalPrediction,
    HfArgumentParser,
    Trainer,
    TrainingArguments,
    default_data_collator,
    set_seed,
)
import json
from tqdm import tqdm

In [4]:
model = AutoModelForSequenceClassification.from_pretrained("sentiment-malay-deberta/checkpoint-88000")

In [3]:
from transformers import pipeline
sentiment_analysis = pipeline("sentiment-analysis",model="sentiment-malay-deberta/checkpoint-88000")
print(sentiment_analysis(["teloq hang","tak prihatin fikir kita ni apa","bossku","macam la dia tu hebat","eh salah","belagak pandai"]))

[{'label': 'negative', 'score': 0.6645314693450928}, {'label': 'negative', 'score': 0.9972461462020874}, {'label': 'positive', 'score': 0.9917457699775696}, {'label': 'positive', 'score': 0.9973276853561401}, {'label': 'negative', 'score': 0.9989587068557739}, {'label': 'negative', 'score': 0.9864065051078796}]


In [11]:
data = []

with open('combined-data-sentiment.jsonl') as f:
    for x in f:
        result = json.loads(x)
        if result['split'] != 'train':
            data.append(result)

In [26]:
batch_size = 3
predicted_labels = []
for i in tqdm(range(0, len(data), batch_size)):
    batch = data[i:i + batch_size]
    batch_predictions = sentiment_analysis([x['text'] for x in batch])

    for predictions in batch_predictions:
        max_score_label = predictions['label']

        predicted_labels.append(max_score_label)

100%|██████████████████████████████████████████████████████████████████████████████████████████| 10857/10857 [15:37<00:00, 11.58it/s]


In [27]:
from sklearn.metrics import classification_report

print(classification_report([x['sentiment'] for x in data],predicted_labels, digits = 5))

/home/aisyah/.local/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1471: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


              precision    recall  f1-score   support

    negative    0.94533   0.97434   0.95962     20108
     neutral    0.00000   0.00000   0.00000       699
    positive    0.92857   0.93505   0.93180     11762

    accuracy                        0.93924     32569
   macro avg    0.62463   0.63646   0.63047     32569
weighted avg    0.91899   0.93924   0.92897     32569



/home/aisyah/.local/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1471: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/aisyah/.local/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1471: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [5]:
model.push_to_hub('deberta-v3-xsmall-malay-sentiment', organization='malaysia-ai', safe_serialization=True)

/home/aisyah/.local/lib/python3.8/site-packages/transformers/utils/hub.py:671: UserWarning: The `organization` argument is deprecated and will be removed in v5 of Transformers. Set your organization directly in the `repo_id` passed instead (`repo_id={organization}/{model_id}`).
  warnings.warn(


model.safetensors:   0%|          | 0.00/283M [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/malaysia-ai/deberta-v3-xsmall-malay-sentiment/commit/544700f30bbb273144933f93417cd87cad9b4c94', commit_message='Upload DebertaV2ForSequenceClassification', commit_description='', oid='544700f30bbb273144933f93417cd87cad9b4c94', pr_url=None, pr_revision=None, pr_num=None)

In [7]:
tokenizer = AutoTokenizer.from_pretrained("sentiment-malay-deberta/checkpoint-88000")

In [8]:
tokenizer.push_to_hub('deberta-v3-xsmall-malay-sentiment', organization='malaysia-ai', safe_serialization=True)

spm.model:   0%|          | 0.00/2.46M [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/malaysia-ai/deberta-v3-xsmall-malay-sentiment/commit/3ecb0599c10fb975720251091ff9b3ef2eced5b7', commit_message='Upload tokenizer', commit_description='', oid='3ecb0599c10fb975720251091ff9b3ef2eced5b7', pr_url=None, pr_revision=None, pr_num=None)

In [9]:
from huggingface_hub import HfApi
api = HfApi()
api.upload_file(
    path_or_fileobj="combined-data-sentiment.jsonl",
    path_in_repo="README.md",
    repo_id="aisyahhrazak/combined-malay-sentiment",
    repo_type="dataset",
)

combined-data-sentiment.jsonl:   0%|          | 0.00/652M [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/datasets/aisyahhrazak/combined-malay-sentiment/commit/9ab06163578a4743a657f66d3b39a38e014d8c4d', commit_message='Upload README.md with huggingface_hub', commit_description='', oid='9ab06163578a4743a657f66d3b39a38e014d8c4d', pr_url=None, pr_revision=None, pr_num=None)